# 1.1 First NGSolve example

Let us solve the Poisson problem of finding $u$ satisfying 

$$
\begin{aligned}
-\Delta u & = f && \text { in  the unit square},
\\
u & = 0 && \text{ on the bottom and right parts of the boundary},
\\
\frac{\partial u }{\partial n } & = 0 
&& \text{ on the remaining  boundary parts}.
\end{aligned}
$$

## Quick steps to solution:

#### 1. Import NGSolve and Netgen Python modules:

In [1]:
from ngsolve import *
from ngsolve.webgui import Draw

#### 2. Generate an unstructured mesh

#### Utiliza la funcionalidad de NGSolve para generar una malla para el dominio del cuadrado unitario

# Aquí, se crea un objeto unit_square, que se asume que es una representación del dominio del cuadrado unitario. El método GenerateMesh() genera una malla para este dominio con cierto tamaño máximo de los elementos definido por maxh=0.1. El parámetro maxh controla el tamaño máximo de los elementos de la malla. En este caso, el valor de 0.1 se refiere a la máxima longitud de los lados de los elementos de la malla.
# 
mesh = Mesh(unit_square.GenerateMesh(maxh=0.1)): Aquí se asigna la malla generada al objeto mesh. Se crea un objeto Mesh que contiene la malla generada para el dominio del cuadrado unitario.# 

mesh.nv, mesh.ne: Estos comandos imprimen el número de vértices y el número de elementos en la malla generada. mesh.nv representa el número de vértices en la malla y mesh.ne es el número de elementos en la malla.

In [2]:
mesh = Mesh(unit_square.GenerateMesh(maxh=0.1))
mesh.nv, mesh.ne   # number of vertices & elements 

(137, 232)

# 137: Representa el número de vértices en la malla generada para el cuadrado unitario.
# 
232: Es el número de elementos en la malla, es decir, la cantidad de subdivisiones o subregiones en las que se divide el cuadrado unitario para formar la malla.

Here we prescribed a maximal mesh-size of 0.2 using the `maxh` flag. 

In [3]:
Draw(mesh);

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.23…

#### 3. Declare a finite element space:

# H1(mesh, order=1, dirichlet="bottom|right"): Aquí se crea un espacio de funciones finitas sobre la malla mesh. El espacio de funciones finitas H1 representa funciones que son continuas y tienen derivadas en $L^2$ 2
  (es decir, sus gradientes están en el espacio de funciones cuadrado-integrables). Este espacio se define sobre la malla mesh. El parámetro order=1 especifica el grado de las funciones (en este caso, funciones lineales), y dirichlet="bottom|right" parece estar indicando que las condiciones de Dirichlet se aplican en los bordes inferiores y derechos de la mal# la.

fes.ndof: Esto devuelve el número de grados de libertad (dof, por sus siglas en inglés "degrees of freedom") en este espacio de funciones finitas. Los grados de libertad son esencialmente el número de incógnitas (número de funciones lineales independientes) en el espacio de funciones finitas. Esto incluiría el número de puntos de interpolación en los elementos de la malla y los grados de libertad restringidos por las condiciones de contorno.

In [4]:
fes = H1(mesh, order=7, dirichlet="bottom|right")
fes.ndof  # number of unknowns in this space

5825

# indica que hay 137 grados de libertad en el espacio de funciones finitas que se ha definido.

Python's help system displays further documentation.

In [5]:
help(fes)

Help on H1 in module ngsolve.comp object:

class H1(FESpace)
 |  An H1-conforming finite element space.
 |
 |  The H1 finite element space consists of continuous and
 |  element-wise polynomial functions. It uses a hierarchical (=modal)
 |  basis built from integrated Legendre polynomials on tensor-product elements,
 |  and Jaboci polynomials on simplicial elements.
 |
 |  Boundary values are well defined. The function can be used directly on the
 |  boundary, using the trace operator is optional.
 |
 |  The H1 space supports variable order, which can be set individually for edges,
 |  faces and cells.
 |
 |  Internal degrees of freedom are declared as local dofs and are eliminated
 |  if static condensation is on.
 |
 |  The wirebasket consists of all vertex dofs. Optionally, one can include the
 |  first (the quadratic bubble) edge basis function, or all edge basis functions
 |  into the wirebasket.
 |
 |  Keyword arguments can be:
 |
 |  order: int = 1
 |    order of finite element 

#### 4. Declare test function, trial function, and grid function 

* Test and trial function are symbolic objects - called `ProxyFunctions` -  that help you construct bilinear forms (and have no space to hold solutions). 

* `GridFunctions`, on the other hand, represent functions in the finite element space and contains memory to hold coefficient vectors.

# u = fes.TrialFunction(): Aquí se define un objeto simbólico u que representa la "función de ensayo" (trial function) en el espacio de funciones finitas fes. La función de ensayo es una función que se utiliza para buscar la solución de la ecuación diferencial en el método de elementos finitos. En esencia, u será la función desconocida que se intentará encontrar para resolver el problema.
# 
v = fes.TestFunction(): De manera similar, se define un objeto simbólico v que representa la "función de test" (test function) en el espacio de funciones finitas fes. La función de test se utiliza en la formulación variacional de la ecuación diferencial para probar la solución propuesta por la función de ensayo. Esta función de test será utilizada en el proceso de resolver la ecuación diferencial por el método de elementos finitos.# 

gfu = GridFunction(fes): Aquí se crea un objeto gfu del tipo GridFunction asociado al espacio de funciones finitas fes. Este objeto gfu será utilizado para almacenar la solución numérica de la ecuación diferencial en la malla. Es decir, contendrá la func 
�
u que satisface la ecuación Poisson sobre la malla.

In [6]:
u = fes.TrialFunction()  # symbolic object
v = fes.TestFunction()   # symbolic object
gfu = GridFunction(fes)  # solution 

Alternately, you can get both the trial and test variables at once:

# TnT Función de aproximación (trial and test) test: función de ponderación

In [7]:
u, v = fes.TnT()

#### 5. Define and assemble linear and bilinear forms:

# a = BilinearForm(fes): Aquí se crea un objeto a del tipo BilinearForm, asociado al espacio de funciones finitas fes. Un BilinearForm se utiliza para representar la forma bilineal asociada al problema. En el contexto de la ecuación de Poisson, la forma bilineal suele involucrar términos que contienen derivadas de la función de ensayo (u) y la función de test (v).
# 
a += grad(u)*grad(v)*dx: Se definen los términos de la forma bilineal. grad(u) y grad(v) representan los gradientes de las funciones u y v, respectivamente. En el problema de Poisson, grad(u) y grad(v) se utilizan para representar las derivadas espaciales de las funciones de ensayo y de test. El término dx indica la integración sobre el dominio.# 

a.Assemble(): Después de definir los términos de la forma bilineal, se utiliza el método Assemble() para ensamblar la matriz asociada a a. Esto implica la evaluación numérica de la integral sobre la malla para obtener la representación matricial de la forma bilinea# l.

f = LinearForm(fes): Similar a la BilinearForm, se crea un objeto f del tipo LinearForm, asociado al espacio de funciones finitas fes. El LinearForm se utiliza para representar la forma lineal asociada al problema. En el contexto de la ecuación de Poisson, la forma lineal suele contener términos lineales en la función de test (v) y posiblemente en las funciones fuente o términos forzantes del probl# ema.

f += x*v*dx: Se definen los términos de la forma lineal. x podría representar un campo escalar (como la función fuente o un término forzante del problema). v es la función de test. dx indica la integración sobre el do# minio.

f.Assemble(): Al igual que con la forma bilineal, el método Assemble() se utiliza para ensamblar la representación numérica de la forma lineal f

In [8]:
a = BilinearForm(fes)
a += grad(u)*grad(v)*dx
a.Assemble()

f = LinearForm(fes)
f += x*v*dx
f.Assemble();

Alternately, we can do one-liners: 

In [9]:
a = BilinearForm(grad(u)*grad(v)*dx).Assemble()
f = LinearForm(x*v*dx).Assemble()

You can examine the linear system in more detail:

In [10]:
print(f.vec)

 4.16667e-05
 0.00259713
 0.001625
 8.94898e-05
 0.000524248
 0.00108866
 0.0014012
 0.00181062
 0.00224583
 0.00260886
 0.00282313
 0.00290497
 0.00327283
 0.00356735
 0.00356399
 0.0039385
 0.00416898
 0.00420942
 0.00422101
 0.00425523
 0.00422508
 0.00490256
 0.00594646
 0.00322428
 0.00326175
 0.00277011
 0.00217396
 0.00166527
 0.00119941
 0.000753088
 0.000396818
 9.47241e-05
 9.32024e-05
 0.00010905
 0.000118838
 0.0001224
 0.000125679
 0.000139174
 0.000206369
 0.000225384
 0.00165026
 0.00238558
 0.00310606
 0.00408058
 0.00499507
 0.00555962
 0.00556139
 0.00519081
 0.00605906
 0.00579454
 0.00698723
 0.00792567
 0.00806885
 0.00795802
 0.00811952
 0.0082474
 0.00844436
 0.00556319
 0.00698973
 0.00665616
 0.00495605
 0.00376814
 0.00285484
 0.00193673
 0.00106455
 0.000515226
 0.000462838
 0.000610731
 0.000707788
 0.000732141
 0.000736791
 0.000749017
 0.000922628
 0.00226065
 0.00162566
 0.00481935
 0.00580575
 0.00604536
 0.00518734
 0.00361145
 0.00782665
 0.00566048
 0

In [11]:
print(a.mat)

Row 0:   0: 1   4: -0.5   39: -0.5   137: -0.0833333   138: 1.70111e-15   139: 8.50448e-16   140: 6.28133e-16   141: 3.01625e-16   142: 1.79761e-16   143: -0.0833333   144: 1.70746e-15   145: 8.51221e-16   146: 6.30111e-16   147: 2.99321e-16   148: 1.83555e-16   203: 0.166667   204: 4.55365e-18   205: -6.20597e-16   206: 1.30104e-18   207: -2.91e-16   208: 4.87891e-19   2345: -9.92997e-16   2346: 1.39882e-15   2347: -1.00526e-15   2348: 7.6481e-16   2349: -4.54077e-16   2350: -1.15535e-18   2351: 2.69992e-18   2352: 2.73422e-18   2353: 2.43945e-19   2354: 4.62988e-16   2355: 2.02773e-16   2356: 1.07055e-16   2357: 1.69407e-18   2358: 3.3983e-18   2359: 2.15973e-16
Row 1:   1: 0.852428   12: -0.305555   13: -0.305283   48: -0.24159   149: -0.0201768   150: 7.17911e-16   151: 3.40636e-16   152: 2.69221e-16   153: 1.12811e-16   154: 7.78457e-17   155: -0.0200882   156: 7.15357e-16   157: 3.39938e-16   158: 2.68882e-16   159: 1.14275e-16   160: 7.55147e-17   161: -0.101806   162: 1.47344e-

#### 6. Solve the system:

In [12]:
gfu.vec.data = \
    a.mat.Inverse(freedofs=fes.FreeDofs()) * f.vec
Draw(gfu);

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.23…

The Dirichlet boundary condition constrains some degrees of freedom. The argument `fes.FreeDofs()` indicates that only the remaining "free" degrees of freedom should participate in the linear solve.

You can examine the coefficient vector of solution if needed:

In [13]:
print((fes.FreeDofs()))
print(gfu.vec)

0: 00010000000000000000001111111111111111111111111111
50: 11111111111111111111111111111111111111111111111111
100: 11111111111111111111111111111111111110000001111110
150: 00000000000111111000000111111111111111111111111000
200: 00011111111111100000011111111111100000011111111111
250: 10000001111111111110000001111111111110000001111111
300: 11111000000111111111111000000111111111111111111111
350: 11100000011111111111100000011111111111100000011111
400: 11111110000001111111111110000001111111111110000001
450: 11111111111000000111111111111000000111111111111111
500: 11111111111111111111111111111111111111111111111111
550: 11111111111111111111111111111111111111111111111111
600: 11111111111111111111111111111111111111111111111111
650: 11111111111111111111111111111111111111111111111111
700: 11111111111111111111111111111111111111111111111111
750: 11111111111111111111111111111111111111111111111111
800: 11111111111111111111111111111111111111111111111111
850: 1111111111111111111111111111111111111111111111

You can see the zeros coming from the zero boundary conditions.

In [14]:
Norm = sqrt(Integrate(gfu**2*dx, mesh))

In [15]:
print(Norm)

0.061393299859351394


## Ways to interact with NGSolve

* A jupyter notebook (like this one) gives you one way to interact with NGSolve. When you have a complex sequence of tasks to perform, the notebook may not be adequate.


* You can write an entire python module in a text editor and call python on the command line. (A script of the above is provided in `poisson.py`.)
    ```
    python3 poisson.py
    ```
  
* If you want the Netgen GUI, then use `netgen` on the command line:
    ```
    netgen poisson.py
    ```
  You can then ask for a python shell from the GUI's menu options (`Solve -> Python shell`).
  